In [2]:
import requests 
import os
import re
from collections import defaultdict
from copy import deepcopy
import pickle
import pandas as pd
import numpy as np
import time

from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
from selenium.webdriver.common.action_chains import ActionChains
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.support.ui import WebDriverWait
from selenium.common.exceptions import NoSuchElementException, ElementNotInteractableException, ElementClickInterceptedException, StaleElementReferenceException

In [43]:
driver_loc = "../webdriver/chromedriver_97"
options = webdriver.ChromeOptions()
driver = webdriver.Chrome(executable_path=driver_loc, options = options)

<ipython-input-43-40e023bc7d3b>:3: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(executable_path=driver_loc, options = options)


In [30]:
category_elems = driver.find_elements(By.XPATH, ".//li[@id='rootCategoryList']")
category_names = [x.find_element(By.XPATH, "button[contains(@class,'button _click')]").text for x in category_elems]

category_buttons = {name : elem for elem, name in zip(category_elems, category_names)}

In [31]:
# 카테고리 더보기 클릭
category_layer = driver.find_element(By.XPATH, ".//div[contains(@class, 'co_category_layer')]").get_attribute("class")
if category_layer == "co_category_layer":
    driver.find_element(By.XPATH, ".//div[@class='co_category_wrap']").click()
else:
    print("Category Wrap is already opened")

In [32]:
# 대분류 카테고리 버튼 
main_category_elems = driver.find_elements(By.XPATH, ".//div[contains(@class,'co_main_category')]//li[@class='co_list']")
main_category_names = [re.sub("\n|(선택됨)","",x.text) for x in main_category_elems]

main_category_buttons = {name : elem for name, elem in zip(main_category_names, main_category_elems)}

In [33]:
# 카테고리 클릭
main_category_buttons["가전"].click()


In [16]:
category_more_button = driver.find_elements(By.XPATH, ".//div[@class='filter_finder_tit__2VCKd' and @data-nclick='N=a:rcc*A.cat.fold']")
if len(category_more_button) != 0:
    category_more_button[0].click()

In [17]:
def extract_catId():
    return re.search(r"catId=([\d]{8})",driver.current_url).group(1)

In [18]:
def extract_category_levels():
    category_infos = driver.find_elements(By.XPATH, ".//div[@class='resultSummary_category_info__1jq2r']/a")
    return [x.text for x in category_infos]

In [60]:
def extract_filter_list():
    category_filter_panel = driver.find_elements(By.XPATH, ".//div[contains(@class,'filter_finder_col__3ttPW')]")
    # if len(category_filter_panel) == 0:
    #     return None, None
    filters = category_filter_panel[0].find_elements(By.XPATH, "div[@class='filter_finder_row__1rXWv']//ul[@class='filter_finder_list__16XU5']/li/a")
    filter_names = [x.text for x in filters]
    return filter_names, filters
    

In [61]:
def check_next_level(prev_filters):
    filter_names, _ = extract_filter_list()
    # if filter_names is None:
    #     return False

    # 기존과 filter들이 동일하면 다음 level의 filter가 없다고 판단
    if prev_filters == filter_names:
        return False
    else:
        return True

In [69]:
get_category_ids()

PC용
https://search.shopping.naver.com/search/category/100005054?catId=50002146&origQuery&pagingIndex=1&pagingSize=40&productSet=total&query&sort=rel&timestamp=&viewType=list#
단품
https://search.shopping.naver.com/search/category/100005054?catId=50002146&origQuery&pagingIndex=1&pagingSize=40&productSet=total&query&sort=rel&timestamp=&viewType=list#
단품+스피커
https://search.shopping.naver.com/search/category/100005172?catId=50002146&origQuery&pagingIndex=1&pagingSize=40&productSet=total&query&sort=rel&timestamp=&viewType=list#
블루투스
https://search.shopping.naver.com/search/category/100005173?catId=50002146&origQuery&pagingIndex=1&pagingSize=40&productSet=total&query&sort=rel&spec=M10021038%7CM105052&timestamp=&viewType=list#


([[],
  ['디지털', '음향기기', '사운드바', '단품'],
  ['디지털', '음향기기', '사운드바', '단품+스피커'],
  ['디지털', '음향기기', '사운드바', '블루투스']],
 ['50001212', '50002146', '50002146', '50002146'])

In [68]:
def get_category_ids():
    category_levels = []
    catIds = []
    filter_names, filters = extract_filter_list()
    for i in range(len(filters)):
    # for i in range(2):
        filters[i].click()
        org_url = driver.current_url
        print(filter_names[i])
        print(org_url)
        time.sleep(1.5)
        # category_levels = extract_category_levels()
        # catId = extract_catId()
        category_levels.append(extract_category_levels())
        catIds.append(extract_catId())

        no_result = driver.find_elements(By.XPATH, ".//div[@class='noResult_no_result__1ad0P']")
        if len(no_result) > 0:
            driver.back()
            time.sleep(1.5)
            filter_names, filters = extract_filter_list()
            continue

        if check_next_level(prev_filters=filter_names):
            print("세부 카테고리 있음")
            temp_category_levels, temp_catIds = get_category_ids()
            category_levels.extend(temp_category_levels)
            catIds.extend(temp_catIds)
            print(temp_category_levels)
            print(temp_catIds)
            driver.get(org_url)
            time.sleep(1.5)
            filter_names, filters = extract_filter_list()

        # if len(category_levels) > 20:
        #     break

    return category_levels, catIds

In [8]:
from Collect_Category_Id import *

In [9]:
options = webdriver.ChromeOptions()
driver = webdriver.Chrome(executable_path=driver_loc, options = options)

NameError: name 'driver_loc' is not defined

In [12]:
category_id = Collect_Category_Ids(driver_loc = "../webdriver/chromedriver_103")
category_levels , category_ids = category_id.get(categories = ["가전", "디지털", "화장품/미용", "컴퓨터"])

NoSuchElementException: Message: no such element: Unable to locate element: {"method":"xpath","selector":".//div[contains(@class, 'co_category_layer')]"}
  (Session info: chrome=103.0.5060.114)
Stacktrace:
Backtrace:
	Ordinal0 [0x006A6463+2188387]
	Ordinal0 [0x0063E461+1762401]
	Ordinal0 [0x00553D78+802168]
	Ordinal0 [0x00581880+989312]
	Ordinal0 [0x00581B1B+989979]
	Ordinal0 [0x005AE912+1173778]
	Ordinal0 [0x0059C824+1099812]
	Ordinal0 [0x005ACC22+1166370]
	Ordinal0 [0x0059C5F6+1099254]
	Ordinal0 [0x00576BE0+945120]
	Ordinal0 [0x00577AD6+948950]
	GetHandleVerifier [0x009471F2+2712546]
	GetHandleVerifier [0x0093886D+2652765]
	GetHandleVerifier [0x0073002A+520730]
	GetHandleVerifier [0x0072EE06+516086]
	Ordinal0 [0x0064468B+1787531]
	Ordinal0 [0x00648E88+1805960]
	Ordinal0 [0x00648F75+1806197]
	Ordinal0 [0x00651DF1+1842673]
	BaseThreadInitThunk [0x76F66739+25]
	RtlGetFullPathName_UEx [0x77DE8FEF+1215]
	RtlGetFullPathName_UEx [0x77DE8FBD+1165]


: 

In [32]:
category_id = Collect_Category_Ids(driver_loc = "../webdriver/chromedriver_99")
category_levels , category_ids = category_id.get(categories = ["가전", "디지털", "화장품/미용"])

<ipython-input-29-a7aa19c16cff>:26: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  self.driver = webdriver.Chrome(executable_path=driver_loc, options = options)


TV
https://search.shopping.naver.com/search/category/100000005#
세부 카테고리 있음
21년/22년형
https://search.shopping.naver.com/search/category/100000580?catId=50001395&origQuery&pagingIndex=1&pagingSize=40&productSet=total&query&sort=rel&timestamp=&viewType=list#
화면크기별
https://search.shopping.naver.com/search/category/100001952?catId=50001395&origQuery&pagingIndex=1&pagingSize=40&productSet=total&query&sort=rel&spec=M10017827%7CM11111911%20M10017827%7CM10851449&timestamp=&viewType=list#
세부 카테고리 있음
80인치 이상
https://search.shopping.naver.com/search/category/100000612?catId=50001395&origQuery&pagingIndex=1&pagingSize=40&productSet=total&query&sort=rel&timestamp=&viewType=list#
70인치대
https://search.shopping.naver.com/search/category/100004806?catId=50001395&origQuery&pagingIndex=1&pagingSize=40&productSet=total&query&sort=rel&spec=M10011351%7CM11064347%20M10011351%7CM11064298%20M10011351%7CM11064357%20M10011351%7CM11064397%20M10011351%7CM11064299%20M10011351%7CM11064387%20M10011351%7CM11064417%20M10

In [34]:
with open("가전_디지털_화장품_카테고리.pkl", "wb") as f:
    pickle.dump({"category_levels" : category_levels, "category_ids" : category_ids}, f)

In [46]:
temp = pd.DataFrame({"category_level" : [" > ".join(y) for x in category_levels for y in x], "category_id" : [y for x in category_ids for y in x]})

In [54]:
pd.concat([temp["category_level"].str.split(" > ", expand=True).rename(columns = {0:"category_1", 1: "category_2", 2 : "category_3", 3: "category_4"}), temp], axis = 1).to_excel("네이버_쇼핑_카테고리.xlsx", index= False)

In [55]:
category_levels_1 = category_levels[:]
catIds_1 = catIds[:]

In [61]:
category_levels.append(["생활/건강", "안마용품"])
catIds.append("50000075")

In [64]:
with open("category_levels_total.pkl", "wb") as f:
    pickle.dump(category_levels, f)

with open("catIds_total.pkl", "wb") as f:
    pickle.dump(catIds, f)

In [49]:
with open("category_levels_total.pkl", "rb") as f:
    category_levels_total = pickle.load(f)

In [10]:
with open("catIds_total.pkl", "rb") as f:
    catIds = pickle.load(f)

In [62]:
category_levels.extend(category_levels_1)
catIds.extend(catIds_1)

In [59]:
category_levels

[['생활/건강', '안마용품', '안마의자'],
 ['생활/건강', '안마용품', '렌탈안마의자'],
 ['생활/건강', '안마용품', '안마기'],
 ['생활/건강', '안마용품', '쿠션안마기'],
 ['생활/건강', '안마용품', '안마매트'],
 ['생활/건강', '안마용품', '기타안마용품']]

In [22]:
category_levels, catIds = get_category_ids()

TV
https://search.shopping.naver.com/search/category/100000005#
세부 카테고리 있음
스마트TV
https://search.shopping.naver.com/search/category/100000580?catId=50001395&origQuery&pagingIndex=1&pagingSize=40&productSet=total&query&sort=rel&timestamp=&viewType=list#
QLEDTV
https://search.shopping.naver.com/search/category/100001953?catId=50001395&origQuery&pagingIndex=1&pagingSize=40&productSet=total&query&sort=rel&spec=M10015967%7CM10787585%20M10015967%7CM10787587%20M10015967%7CM10787591%20M10015967%7CM10787593%20M10015967%7CM10030201%20M10015967%7CM10779257%20M10015967%7CM10787597%20M10015967%7CM10779086%20M10015967%7CM10779085%20M10015967%7CM10787612%20M10015967%7CM10778810%20M10015967%7CM10796741%20M10015967%7CM10830008%20M10015967%7CM10840007%20M10015967%7CM10841724%20M10015967%7CM10832974%20M10015967%7CM10865085%20M10015967%7CM10830728%20M10015967%7CM10034057&timestamp=&viewType=list#
OLEDTV
https://search.shopping.naver.com/search/category/100000605?catId=50009100&origQuery&pagingIndex=1&pagin

AttributeError: 'NoneType' object has no attribute 'group'

In [50]:
category_levels_total[0][-1]

'안마의자'

In [47]:
len(catIds)

838

In [320]:
total_product_infos = get_product_infos_in_category(cat_ids = catIds, collect_num = 100, image_save = True)  # 96m31s

In [111]:
total_product_infos = get_product_infos_in_category(cat_ids = catIds, cat_names = category_levels_total, collect_num = 100, image_save = False) # 19m 351s

In [125]:
pd_product_info = pd.DataFrame(total_product_infos)
pd_product_info = pd_product_info[['searchCategoryId', 'searchCategoryName', 'rank', 'id', 'productName', 'scoreInfo', 'category1Id', 'category2Id',
                             'category3Id', 'category4Id', 'category1Name', 'category2Name',
                             'category3Name', 'category4Name', 'maker', 'makerNo', 'brand',
                             'brandNo', 'price', 'priceUnit', 'lnchYm', 'productAttr', 'imageName', 'crUrl', 'imageUrl']]

In [126]:
pd_product_info.to_excel("raw_product_infos.xlsx", index = False)

In [ ]:
["영상가전", ]

In [127]:
[catIds[i] for i, x in enumerate(category_levels_total) if x[-1] in ["OLEDTV", "블루투스스피커", "무선청소기", "양문형냉장고", "스탠드형에어컨", "안마의자"]]

['50001828', '50002115', '50002322', '50002350', '50002558', '50002521']

In [128]:
sample_cat_ids = [catIds[i] for i, x in enumerate(category_levels_total) if x[-1] in ["OLEDTV", "블루투스스피커", "무선청소기", "양문형냉장고", "스탠드형에어컨", "안마의자"]]
pd_sample_product_info = pd_product_info.loc[pd_product_info["searchCategoryId"].isin(sample_cat_ids)]

In [129]:
pd_sample_product_info = pd_product_info.loc[pd_product_info["searchCategoryId"].isin(sample_cat_ids)]

In [130]:
pd_sample_product_info.to_excel("raw_sample_product_infos.xlsx", index = False)

In [22]:
pd.DataFrame(total_product_infos).groupby("searchCategoryId").size().sort_values()

searchCategoryId
50002740      1
50001507      1
50003147      1
50001510      1
50001503      1
           ... 
50001987    100
50001988    100
50001991    100
50001996    100
50009240    100
Length: 800, dtype: int64

In [54]:
def get_product_infos_in_category(cat_ids:list, cat_names: list, collect_num:int = None, image_save:bool = False):
    if isinstance(cat_ids, list) == False:
        cat_ids = [cat_ids]
    base_url = "https://search.shopping.naver.com/api/search/category"
    total_product_infos = defaultdict(list)

    for cat_id, cat_name in zip(cat_ids, cat_names):
        initial_params = create_params(idx=1, page_size=40, cat_id=cat_id)

        initial_rq = requests.get(base_url, params = initial_params)

        initial_rq_json = initial_rq.json()

        total_num = initial_rq_json["shoppingResult"]["total"]
        
        if collect_num is None:
            temp_collect_num = total_num
        else:
            temp_collect_num = min(collect_num, total_num)

        max_page, remainder = get_max_page(initial_rq_json, collect_num = temp_collect_num, page_size = 80)
        for pg in range(1, max_page+1):
            params = create_params(idx=pg, page_size=80, cat_id=cat_id)
            rq = requests.get(base_url, params = params)
            rq_json = rq.json()

            if pg < max_page:
                collect_num_in_page = None

            else:
                collect_num_in_page = remainder

            try:
                products_infos = extract_product_infos(rq_json, collect_num_in_page, image_save = image_save, img_dir = f"./images/{cat_id}/")
                products_infos["searchCategoryId"] = [cat_id for x in range(len(products_infos["id"]))]
                products_infos["searchCategoryName"] = [" > ".join(cat_name) for x in range(len(products_infos["id"]))]
            except:
                print(rq.url)

            total_product_infos = merge_dict(total_product_infos, products_infos)
    
    return total_product_infos

In [55]:
def create_params(idx:int, page_size:int, cat_id:str):
    params = {"sort" : "rel",
              "pagingIndex" : idx,
              "pagingSize" : page_size,
              "viewType" : "list",
              "productSet" : "model",
              "catId" : cat_id,
              "deliveryFee" : "",
              "deliveryTypeValue" : "",
              "frm" : "NVSHMDL",
              "iq" : "",
              "eq" : "",
              "xq" : ""}
    return params

In [56]:
def get_max_page(rq_json:dict, collect_num:int, page_size:int = 80):
    
    max_page = int(np.ceil(collect_num / page_size))
    remainder = int(collect_num % page_size)

    return max_page, remainder

In [61]:
def merge_dict(org_dict:dict, new_dict:dict, type:str = "full"):
    merged_dict = deepcopy(org_dict)
    if type == "full":
        keys = pd.unique(list(org_dict.keys()) + list(new_dict.keys()))
    elif type == "left":
        keys = list(org_dict.keys())
    elif type == "right":
        keys = list(new_dict.keys())


    for key in keys:
        if isinstance(new_dict[key], list):
            merged_dict[key].extend(new_dict[key])
        else:
            merged_dict[key].append(new_dict[key])
    
    return merged_dict

In [95]:
def concat_dict(input_dict:dict) -> str:
    temp = []
    for k, v in input_dict.items():
        v = [str(x) for x in v]
        temp.append(f"{k} : {', '.join(v)}")
    return " | ".join(temp)

In [96]:
def create_productAttr(attr_val, char_val):
    product_attr_dict = defaultdict(list)
    for attr, char in zip(attr_val, char_val):     
        product_attr_dict[attr].append(char)

    return concat_dict(product_attr_dict)

In [110]:
def extract_product_infos(rq_json:dict, collect_num:int = None, image_save:bool = True, img_dir:str = "./image/") -> dict:
    
    products_dict = defaultdict(list)
    products = rq_json["shoppingResult"]["products"]

    if collect_num is None:
        collect_num = len(products)

    for i, product in enumerate(products):
        if i == collect_num:
            break
        products_dict["rank"].append(product["rank"])
        products_dict["id"].append(product["id"])
        products_dict["scoreInfo"].append(product["scoreInfo"])
        products_dict["productName"].append(product["productName"])
        products_dict["category1Id"].append(product["category1Id"])
        products_dict["category2Id"].append(product["category2Id"])
        products_dict["category3Id"].append(product["category3Id"])
        products_dict["category4Id"].append(product["category4Id"])
        products_dict["category1Name"].append(product["category1Name"])
        products_dict["category2Name"].append(product["category2Name"])
        products_dict["category3Name"].append(product["category3Name"])
        products_dict["category4Name"].append(product["category4Name"])
        products_dict["maker"].append(product["maker"])
        products_dict["makerNo"].append(product["makerNo"])
        products_dict["brand"].append(product["brand"])
        products_dict["brandNo"].append(product["brandNo"])
        products_dict["price"].append(product["price"])
        products_dict["priceUnit"].append(product["priceUnit"])
        products_dict["lnchYm"].append(product["lnchYm"])
        products_dict["attributeValue"].append(product["attributeValue"])
        products_dict["characterValue"].append(product["characterValue"])
        products_dict["crUrl"].append(product["crUrl"])
        products_dict["imageUrl"].append(product["imageUrl"])
        try: 
            products_dict["imageName"].append(product["imageUrl"].split("/")[-1])
            # re.search(r"main_[\d]{7}/([\d]{10,11}\.[\d]{14})", product["imageUrl"]).group(1) + ".jpg"
        except:
            print(product["imageUrl"])
            
        

        attr_val = re.sub(r"_[A-Z]{1}","",product["attributeValue"]).split("|")
        char_val = product["characterValue"].split("|")
        attr_char = create_productAttr(attr_val, char_val)
        products_dict["productAttr"].append(attr_char)

        if image_save:
            save_images(img_urls=product["imageUrl"], 
                        img_names=product["imageUrl"].split("/")[-1],
                        img_dir = img_dir)
    
    return products_dict

In [93]:
re.search(r"main_[\d]{7}/([\d]{11}\.[\d]{14})", total_product_infos["imageUrl"][0]).group(1)

'24895107748.20210607141246'

In [86]:
total_product_infos["imageUrl"][0]
total_product_infos["characterValue"][0]

'어깨|팔|허리|엉덩이|골반|종아리|발|손|허벅지|목|등|S프레임|L프레임|8종류|리클라이닝|다리길이|슬라이딩|안마속도|안마볼위치|자동체형인식|온열기능|발바닥지압롤러|블루투스스피커|자동타이머|리모컨|이동바퀴|내피분리|외피분리|주무름|문지름|두드림|공기압|롤링|지압|종아리|등|취침모드|스트레칭모드|상체집중모드|하체집중모드|무중력안마|퀵모드|100w|10cm'

In [416]:
url = "https://search.shopping.naver.com/catalog/20897743509?NaPm=ct%3Dkxdgn5zk%7Cci%3Db1327f480647e353b37cf65463828da46e69500e%7Ctr%3Dslsl%7Csn%3D95694%7Chk%3Dd2b38e8fc84b5684a3c1dd5897b9c9e23d1501bb"
rq = requests.get(url)
soup = BeautifulSoup(rq.text, "html.parser")

In [438]:
aside_1 = []
aside_2 = []
for x in pd_product_info["crUrl"][:10]:
    
    driver.get(x)
    aside_1.append([x.get_attribute("data-i")for x in driver.find_elements(By.XPATH, ".//a[@class='asideBrand_title__39bqM']")])
    aside_2.append([x.get_attribute("data-i")for x in driver.find_elements(By.XPATH, ".//a[@class='asideProduct_title__3R4Xl']")])

In [440]:
60000 / 60 / 60

16.666666666666668

In [434]:
driver.get(url)

In [432]:
[x.get_attribute("data-i")for x in driver.find_elements(By.XPATH, ".//a[@class='asideBrand_title__39bqM']")]

['11204437776', '20771379010', '8857623751', '25040368522', '25169689522']

In [433]:
[x.get_attribute("data-i")for x in driver.find_elements(By.XPATH, ".//a[@class='asideProduct_title__3R4Xl']")]

['82432436374', '21645739444', '82883002760']

In [418]:
soup.find_all("div", attr={"class":"asideBrand_brand_info__2YfhT"})

[]

In [114]:
def save_images(img_urls, img_names, img_dir = "./image/"):
    if isinstance(img_urls, list) == False:
        img_urls = [img_urls]
    if isinstance(img_names, list) == False:
        img_names = [img_names]
    
    if img_dir is None:
        img_dir = f"./image/"
    
    if not os.path.exists(img_dir):
        os.makedirs(img_dir)

    error_list = []
    for img_url, img_name in zip(img_urls, img_names):
        # image 저장
        try:
            img_rq = requests.get(img_url, verify = True)
            with open(f"{img_dir}/{img_name}", "wb") as f:
                f.write(img_rq.content)
        except: 
            error_list.append(img_name)
            print(img_name)

### 모델명 추출

In [4]:
data = pd.read_excel("raw_sample_product_infos.xlsx")

In [8]:
import re

In [72]:
last_token = data["productName"].str.split(" ").apply(lambda x: x[-1])
data["productModel"] = np.where(last_token.str.contains(r"[가-힣]") == False, last_token, None)
data["productModel"].head()

0     LS-6700N
1    HCW-6000S
2      LS-2900
3     HCW-5000
4         None
Name: productModel, dtype: object

In [ ]:
http://www.safetykorea.kr/openapi/api/cert/certificationDetail.json?certNum=XL090008-20314F

In [86]:
def get_kc_info(model_name:str, api_key:str):
    result_dict = defaultdict(list)
    request_headers = {"AuthKey" : api_key}

    request_parameters = {"conditionKey" : "modelName",
                          "conditionValue" : model_name}
    kc_info_base_url = "http://www.safetykorea.kr/openapi/api/cert/certificationList.json"

    kc_info_rq = requests.get(url = kc_info_base_url, headers = request_headers, params = request_parameters)
    kc_info_rq_json = kc_info_rq.json()

    for x in kc_info_rq_json["resultData"]:
        result_dict = merge_dict(result_dict, x)
    
    return result_dict

In [87]:
def get_kc_info_details(cert_num:str, api_key:str):
    request_parameters = {"certNum" : cert_num}
    kc_details_info_base_url = "http://www.safetykorea.kr/openapi/api/cert/certificationDetail.json"
    kc_details_rq = requests.get(url = kc_details_info_base_url, headers = request_headers, params = request_parameters)
    return kc_details_rq.json()

In [107]:
def get_derivative_models(product_model):
    if product_model is None:
        return None
    print(f"idx : {i}, model : {product_model}")
    kc_info_dict = get_kc_info(model_name = product_model, api_key = API_KEY)

    if len(kc_info_dict) == 0:
        return None
        
    kc_info = pd.DataFrame(kc_info_dict)
    cert_num = kc_info.sort_values("certDate", ascending=False).head(1)["certNum"][0]

    kc_info_details_dict = get_kc_info_details(cert_num = cert_num, api_key = API_KEY)

    derivative = kc_info_details_dict["resultData"]["derivationModels"]
    return derivative

In [ ]:
temp = data["productModel"].apply(get_derivative_models)

In [181]:
derivative_list_old = derivative_list[:]

In [186]:
derivative_dict = defaultdict(list)
for x in derivative_list:
    if x is not None:
        derivative_dict["cert_num"].append(x[0])
        derivative_dict["cert_date"].append(x[1])
        derivative_dict["model_name"].append(x[2])
        derivative_dict["product_name"].append(x[3])
        derivative_dict["category_name"].append(x[4])

        if x[5] is not None:
            if len(x[5]) == 0:
                derivative_dict["derivative"].append(None)
            else:
                derivative_dict["derivative"].append(", ".join(x[5]))
        else:
            derivative_dict["derivative"].append(None)        

    else:
        derivative_dict["cert_num"].append(None)
        derivative_dict["cert_date"].append(None)
        derivative_dict["model_name"].append(None)
        derivative_dict["product_name"].append(None)
        derivative_dict["category_name"].append(None)
        derivative_dict["derivative"].append(None)

In [ ]:
pd.concat([data, pd.DataFrame(derivative_dict)], axis = 1)

In [162]:
derivatives = []
for x in derivative_list:
    if x is not None:
        if len(x) == 0:
            derivatives.append("")
        else:
            derivatives.append(", ".join(x))
    else:
        derivatives.append("")        


In [261]:
line = "idx : 21, model : EP-MA102 Not Exist"
re.search(r"model : (.*)\s(Not)+(Exist)", line).group(1)

AttributeError: 'NoneType' object has no attribute 'group'

In [218]:
re.search(r"idx : ([\d])", line).group(1)

'1'

In [268]:
idx_list = []
model_name_list = []
with open("crawl_logs", "r") as f:
    lines = f.readlines()
    for line in lines:
        idx = re.search(r"idx : ([\d]{1,4})", line).group(1)
        if "model-revised" in line:
            model_name = re.search(r"model-revised : (.*)\s[a-z|A-Z]", line).group(1)
        else:
            model_name = re.search(r"model : ([a-z|A-Z|\d|-]*)\s", line).group(1)
        
        idx_list.append(int(idx))
        model_name_list.append(model_name)

AttributeError: 'NoneType' object has no attribute 'group'

In [264]:
model_name_df = pd.DataFrame({"model_name" : model_name_list}, index= idx_list)

In [265]:
model_name_df.head(20)

model_name
0    LS-6700N Exist cert_num : HU071842-21041B
1    HCW-6000S Exist cert_num : HU07595-18026C
2      LS-2900 Exist cert_num : CA021H014-1039
3     HCW-5000 Exist cert_num : HU07982-18033D
6      LSE-20 Exist cert_num : HU072203-20003C
7      ZPC2090 Exist cert_num : HU07656-21066A
8     HT-N02A Exist cert_num : HU072671-20001A
10  HCW-5500S Exist cert_num : HU072097-18004C
11   HCW-5900 Exist cert_num : HU072097-18004C
12   HCW-5600 Exist cert_num : HU072097-18004C
13    ZPC2033 Exist cert_num : HU072527-19001D
14        in9 Exist cert_num : HU071694-21019A
15   LS-7900N Exist cert_num : HU072203-20003C
18    HCW-6100 Exist cert_num : HU07595-18026C
19      LSE-30 Exist cert_num : HU07982-19038A
20    HT-N03A Exist cert_num : HU072671-20002A
21                                EP-MA102 Not
23    HT-N06B Exist cert_num : HU071439-20028A
24    HT-K12A Exist cert_num : HU071842-20027A
26  CMC-X3500 Exist cert_num : HU072450-19002F

In [235]:
pd.concat([data.join(model_name_df), pd.DataFrame(derivative_dict)], axis = 1).to_excel("sample_data_derivative.xlsx", index = False)

In [163]:
data["derivative"] = derivatives

In [164]:
data.to_excel("data_deriv.xlsx", index = False)

In [ ]:
last_token = data["productName"].str.split(" ").apply(lambda x: x[-1])
data["productModel"] = np.where(last_token.str.contains(r"[가-힣]") == False, last_token, None)
data["productModel"].head()

In [135]:
re.search(r"[가-힣]", "rkdk") is None

True

In [174]:
"dff ".strip()

'dff'

In [179]:
product_name = "RF85A9111T1 (브라우니실버) (dfdf)"
re.subn(r"\(.*\)|", "", product_name)[0].strip().split(" ")

['RF85A9111T1']

In [180]:
derivative_list = []
cert_num_list = []
for i, product_name in enumerate(data["productName"]):
    product_model = ""
    tokens = re.subn(r"\(.*\)|", "", product_name)[0].strip().split(" ")
    if re.search(r"[가-힣]",tokens[-1]) is None:
        product_model = tokens[-1]
    else:
        derivative_list.append(None)
        continue

    if product_model is None:
        derivative_list.append(None)
        continue
    if len(product_model) <= 2:
        derivative_list.append(None)
        continue
    
    print(f"idx : {i}, model : {product_model}", end = " ")
    kc_info_dict = get_kc_info(model_name = product_model, api_key = API_KEY)

    if len(kc_info_dict) == 0:
        if len(tokens) > 1:
            if re.search(r"[가-힣]",tokens[-2]) is None:
                product_model = "-".join(tokens[-2:])
                print(f", model-revised : {product_model}", end=" ")
            kc_info_dict = get_kc_info(model_name = product_model, api_key = API_KEY)
            if len(kc_info_dict) == 0:
                print(f"Not Exist")
                derivative_list.append(None)
                continue
        else:
            print("Not Exist")
            derivative_list.append(None)
            continue
    
    print(f"Exist", end = " ")
    
    kc_info = pd.DataFrame(kc_info_dict)
    cert_num = kc_info.sort_values("certDate", ascending=False).head(1)["certNum"][0]

    print(f"cert_num : {cert_num}", end = " ")
    kc_info_details_dict = get_kc_info_details(cert_num = cert_num, api_key = API_KEY)

    derivative = kc_info_details_dict["resultData"]["derivationModels"]
    cert_date = kc_info_details_dict["resultData"]["certDate"]
    model_name = kc_info_details_dict["resultData"]["modelName"]
    product_name = kc_info_details_dict["resultData"]["productName"]
    category_name = kc_info_details_dict["resultData"]["categoryName"]
    
    derivative_list.append((product_model, cert_num, cert_date, model_name, product_name, category_name, derivative))
    print(f"derivatives : {len(derivative)}")

idx : 0, model : LS-6700N Exist cert_num : HU071842-21041B derivatives : 2
idx : 1, model : HCW-6000S Exist cert_num : HU07595-18026C derivatives : 6
idx : 2, model : LS-2900 Exist cert_num : CA021H014-1039 derivatives : 0
idx : 3, model : HCW-5000 Exist cert_num : HU07982-18033D derivatives : 11
idx : 6, model : LSE-20 Exist cert_num : HU072203-20003C derivatives : 5
idx : 7, model : ZPC2090 Exist cert_num : HU07656-21066A derivatives : 9
idx : 8, model : HT-N02A Exist cert_num : HU072671-20001A derivatives : 3
idx : 10, model : HCW-5500S Exist cert_num : HU072097-18004C derivatives : 5
idx : 11, model : HCW-5900 Exist cert_num : HU072097-18004C derivatives : 5
idx : 12, model : HCW-5600 Exist cert_num : HU072097-18004C derivatives : 5
idx : 13, model : ZPC2033 Exist cert_num : HU072527-19001D derivatives : 33
idx : 14, model : in9 Exist cert_num : HU071694-21019A derivatives : 3
idx : 15, model : LS-7900N Exist cert_num : HU072203-20003C derivatives : 5
idx : 18, model : HCW-6100 Exi

In [149]:
for i, product_name in enumerate(data["productName"]):
    if data["derivatives"].str.contains(product_name)

[['LS-6800N ', 'A303H'],
 ['HCW-6000S', 'HCW-6100', 'HCW-6200', 'HCW-6300', 'HCW-6400', 'HCW-6500'],
 [],
 ['HCW-5000s',
  'HCW-5100',
  'HCW-5200',
  'HCW-5300',
  'HCW-5400',
  'HCW-B5000',
  'HCW-B5000S',
  'HCW-B5100',
  'HCW-B5200',
  'HCW-B5300',
  'HCW-B5400'],
 None,
 None,
 ['LS-7901N', 'LSE-20N', 'LSE-25N', 'LSE-26N', 'LSE-27N'],
 ['ZPC3161',
  'ZPC3162',
  'ZPC2090',
  'ZPC2091',
  'ZPC2092',
  'ZPC2093',
  'ZPC2094',
  'ZPC2095',
  'ZPC2096'],
 ['HT-N02B', 'HT-N02C', 'HT-N02D'],
 None,
 ['HCW-5500S', 'HCW-5600', 'HCW-5700', 'HCW-5800', 'HCW-5900'],
 ['HCW-5500S', 'HCW-5600', 'HCW-5700', 'HCW-5800', 'HCW-5900'],
 ['HCW-5500S', 'HCW-5600', 'HCW-5700', 'HCW-5800', 'HCW-5900'],
 ['ZPC2031',
  'ZPC2032',
  'ZPC2033',
  'ZPC2034',
  'ZPC2035',
  'ZPC2036',
  'ZPC2037',
  'ZPC2038',
  'ZPC2039',
  'ZPC2040',
  'ZPC2041',
  'ZPC2042',
  'ZPC2043',
  'ZPC3130',
  'ZPC3131',
  'ZPC3132',
  'ZPC3133',
  'ZPC3134',
  'ZPC3135',
  'ZPC2044',
  'ZPC2045',
  'ZPC2046',
  'ZPC2047',
  'ZPC

In [63]:
API_KEY = "e3225ba6-895a-432c-8b9e-20fed2a64be5"
request_headers = {"AuthKey" : API_KEY}

In [73]:
request_parameters = {"conditionKey" : "modelName",
                      "conditionValue" : data["productModel"][1]}
kc_info_base_url = "http://www.safetykorea.kr/openapi/api/cert/certificationList.json"
rq = requests.get(url = kc_info_base_url, headers = request_headers, params = request_parameters)

In [75]:
result_dict = defaultdict(list)
rq_json = rq.json()

for x in rq_json["resultData"]:
    result_dict = merge_dict(result_dict, x)

In [60]:
certNum = pd.DataFrame(result_dict).sort_values("certDate", ascending=False).head(1)["certNum"][0]

In [68]:
request_parameters = {"certNum" : certNum}
kc_details_info_base_url = "http://www.safetykorea.kr/openapi/api/cert/certificationDetail.json"
kc_details_rq = requests.get(url = kc_details_info_base_url, headers = request_headers, params = request_parameters)

In [71]:
kc_details_rq.json()["resultData"]["derivationModels"]

['LS-6800N ', 'A303H']

In [ ]:
# 카테고리 정보 다시 불러오는 코드

In [16]:
raw_product_infos = pd.read_excel("raw_product_infos.xlsx")

In [17]:
unq_category_ids = raw_product_infos[["searchCategoryId"]].drop_duplicates()["searchCategoryId"].tolist()
unq_category_levels = raw_product_infos[["searchCategoryName"]].drop_duplicates()["searchCategoryName"].tolist()
unq_category_levels = [x.split(" > ")for x in unq_category_levels]

del raw_product_infos

In [3]:
with open("category_ids.pkl", "wb") as f:
    pickle.dump(unq_category_ids, f)

with open("category_levels.pkl", "wb") as f:
    pickle.dump(unq_category_levels, f)

NameError: name 'unq_category_ids' is not defined

In [2]:
from Crawl_Naver_Shopping import *
import pickle

In [3]:
with open("category_ids_220721.pkl", "rb") as f:
    unq_category_ids = pickle.load(f)

with open("category_levels_220721.pkl", "rb") as f:
    unq_category_levels = pickle.load(f)

In [4]:

# 스탠드 제품 코드 추가
stand_ids = ["50003330", "50003331"]
stand_levels = [["가구/인테리어", "조명/스탠드", "스탠드", "단스탠드"], 
 ["가구/인테리어", "조명/스탠드", "스탠드", "장스탠드"]]

unq_category_ids.extend(stand_ids)
unq_category_levels.extend(stand_levels)

In [5]:
category_list = ["LEDTV", "OLEDTV", "LCDTV", "QLEDTV", "DLP", "LCD", "LCoS/기타", 
"퍼스널뷰어", "블루레이플레이어", "사운드바시스템", "단일형홈시어터", 
"조합형홈시어터", "일체형오디오", "스피커단품", "스피커세트", "블루투스스피커", 
"블루투스이어폰/이어셋", "블루투스헤드폰/헤드셋", "이어폰", "헤드폰", 
"일반세탁기", "드럼세탁기", "미니세탁기", "세탁기+건조기", "의류건조기", 
"신발건조기", "탈수기", "유선청소기", "무선청소기", "스팀청소기", 
"로봇청소기", "물걸레청소기", "연수기", "단스탠드", "장스탠드", "의류관리기", 
"스팀다리미", "보풀제거기", "전동칫솔", "구강세정기", "칫솔살균기", 
"전신건조기", "드라이어", "고데기", "매직기", "에어브러시", "남성용면도기", 
"여성용면도기", "두피케어기기", "제모기", "양문형냉장고", "일반형냉장고", 
"스탠드형", "냉동고", "와인냉장고", "화장품냉장고", "쌀냉장고", "제빙기", 
"일반가스레인지", "일반밥솥", "전자레인지", "전기오븐", "복합형오븐", "인덕션",
"핫플레이트", "하이라이트", "하이브리드", "식기세척기", "식기건조기", "무선포트", 
"유선포트", "냉정수기", "냉온정수기", "에스프레소머신", "캡슐/POD머신", 
"팝업토스터기", "오븐토스터기", "음식물처리기", "제빵기", "거품/반죽기", 
"전기그릴", "생선그릴", "쥬서기/녹즙기", "핸드블렌더", "슬로우쿠커", "전기냄비", 
"전기찜기", "튀김기", "전기팬", "샌드위치제조기", "와플제조기", "탄산수제조기", 
"에어프라이어", "믹서기", "전기담요", "전기방석", "전기요", "황토매트", "카페트매트", 
"옥매트", "기타전기매트", "전기장판", "전기온풍기", "가스온풍기", "석유온풍기", "돈풍기", 
"가스보일러", "석유보일러", "전기보일러", "전기온수기", "가스온수기", "라디에이터", 
"컨벡터", "스탠드형에어컨", "벽걸이형에어컨", "멀티형에어컨", "창문형에어컨", "일반용제습기", 
"냉온풍기", "자연식가습기", "가열식가습기", "초음파식가습기", "복합식가습기", "공기청정기", 
"에어워셔", "일반용냉풍기", "스탠드형선풍기", "탁상형선풍기", "휴대용선풍기", "천장형선풍기", 
"전기히터", "석유히터", "가스히터", "연탄/화목난로", "안마의자", "안마기"]
print(f"length of sample category list : {len(category_list)}")

length of sample category list : 136


In [6]:
sample_cat_ids = [unq_category_ids[i] for i, x in enumerate(unq_category_levels) if x[-1] in category_list]
print(f"length of sample cat ids : {len(sample_cat_ids)}")
sample_cat_levels = [x for i, x in enumerate(unq_category_levels) if x[-1] in category_list]
print(f"length of sample cat levels : {len(sample_cat_levels)}")

length of sample cat ids : 138
length of sample cat levels : 138


In [7]:
crawl = Crawl_Naver_Shopping(list_type="가격비교")

In [15]:
crawl = Crawl_Naver_Shopping(list_type="가격비교")
crawl_result = crawl.get_product_infos_in_category(cat_ids = unq_category_ids, cat_levels = unq_category_levels)

['디지털/가전', '노트북']


100%|██████████| 100/100 [00:58<00:00,  1.71it/s]


['디지털/가전', '노트북액세서리']


100%|██████████| 100/100 [00:59<00:00,  1.68it/s]


['디지털/가전', '노트북액세서리', '노트북가방/케이스']


...

['디지털/가전', '노트북액세서리', '노트북받침대/쿨러']


100%|██████████| 9/9 [00:06<00:00,  1.39it/s]


['디지털/가전', '노트북액세서리', '노트북보호필름']


 24%|██▍       | 16/66 [00:11<00:37,  1.34it/s]


ConnectionError: HTTPConnectionPool(host='stopit', port=80): Max retries exceeded with url: / (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x0000021F17C80E80>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))

In [7]:
pd.DataFrame(crawl_result).to_excel("네이버_쇼핑_크롤링_220426.xlsx", index =False)

In [ ]:
crawl = Crawl_Naver_Shopping(list_type="가격비교")
crawl_result = crawl.get_product_infos_in_category(cat_ids = stand_ids, cat_levels = stand_levels, collect_num=None)

In [6]:
light_stand_df = pd.read_excel("조명_스탠드_수집_220401.xlsx")
digital_df  = pd.read_excel("가전_디지털_220401.xlsx")

In [7]:
product_data = pd.concat([digital_df.drop_duplicates("id"), light_stand_df.drop_duplicates("id")], axis = 0)

In [10]:
# pd_crawl_result = pd.DataFrame(crawl_result)
product_data = product_data[['searchCategoryId', 'searchCategoryName', 'id', 'productName', 'scoreInfo', 'category1Id', 'category2Id',
                             'category3Id', 'category4Id', 'category1Name', 'category2Name',
                             'category3Name', 'category4Name', 'maker', 'makerNo', 'brand',
                             'brandNo', 'price', 'priceUnit', 'lnchYm', 'productAttr', 'imageName', 'crUrl', 'imageUrl']]

In [ ]:
product_data.to_excel("네이버_쇼핑_크롤링_220404.xlsx", index = False)

In [13]:
product_data.loc[(product_data["maker"].isna() == False) & (product_data["brand"].isna() == False) & (product_data["productAttr"] != " : ")]

searchCategoryId             searchCategoryName           id  \
0              50001828            생활/건강 > 안마용품 > 안마의자  24895107748   
1              50001828            생활/건강 > 안마용품 > 안마의자  15383106245   
3              50001828            생활/건강 > 안마용품 > 안마의자  22542865736   
4              50001828            생활/건강 > 안마용품 > 안마의자  26518292728   
5              50001828            생활/건강 > 안마용품 > 안마의자  16924785110   
...                 ...                            ...          ...   
96099          50003331  가구/인테리어 > 조명/스탠드 > 스탠드 > 장스탠드  22860818449   
96579          50003331  가구/인테리어 > 조명/스탠드 > 스탠드 > 장스탠드   7504279602   
97600          50003331  가구/인테리어 > 조명/스탠드 > 스탠드 > 장스탠드  25720137579   
98408          50003331  가구/인테리어 > 조명/스탠드 > 스탠드 > 장스탠드  29453994618   
99122          50003331  가구/인테리어 > 조명/스탠드 > 스탠드 > 장스탠드  10552545824   

                   productName  scoreInfo  category1Id  category2Id  \
0         이지움 노블 안마의자 LS-6700N        4.8     50000008     50000075   
1          이지움 벨라 안마의자 LS-2900        4.8     50000008     50000075   
3             컴포어 안마의자 HT-N02A        4.7     50000008     50000075   
4             컴마 안마의자  HT-N06A        4.8     50000008     50000075   
5          뉴블리스 안마의자 HCW-6000S        4.8     50000008     50000075   
...                        ...        ...          ...          ...   
96099          코이 장스탠드 SS-3400        4.7     50000004     50000108   
96579                 유니온 장스탠드        4.7     50000004     50000108   
97600      델라 주름갓 장스탠드 SS-5120        4.5     50000004     50000108   
98408     브리나 유리갓 장스탠드 SS-3720        4.8     50000004     50000108   
99122  원통형 한지 플로어 장스탠드 SS-5300        4.6     50000004     50000108   

       category3Id  category4Id category1Name  ... makerNo brand brandNo  \
0         50001828          NaN         생활/건강  ...  191573    리쏘  149453   
1         50001828          NaN         생활/건강  ...  191573    리쏘  149453   
3         50001828          NaN         생활/건강  ...    7755   휴테크  137710   
4         50001828          NaN         생활/건강  ...    7755   휴테크  137710   
5         50001828          NaN         생활/건강  ...  212668   웰모아  212667   
...            ...          ...           ...  ...     ...   ...     ...   
96099     50001118   50003331.0       가구/인테리어  ...    3799  스피아노  105000   
96579     50001118   50003331.0       가구/인테리어  ...  190598   아뜨레  179486   
97600     50001118   50003331.0       가구/인테리어  ...    3799  스피아노  105000   
98408     50001118   50003331.0       가구/인테리어  ...    3799  스피아노  105000   
99122     50001118   50003331.0       가구/인테리어  ...    3799  스피아노  105000   

         price  priceUnit      lnchYm  \
0      1153190        KRW  20201118.0   
1       635530        KRW  20220101.0   
3      1250000        KRW  20200401.0   
4      1080000        KRW  20210301.0   
5      1230000        KRW  20190107.0   
...        ...        ...         ...   
96099    36500        KRW  20200514.0   
96579    79000        KRW         NaN   
97600    26290        KRW  20210123.0   
98408    94000        KRW  20210901.0   
99122    29900        KRW  20141001.0   

                                             productAttr  \
0      안마부위 : 어깨, 팔, 허리, 엉덩이, 골반, 종아리, 발, 손, 허벅지, 목, ...   
1      안마부위 : 허리, 엉덩이, 골반, 종아리, 허벅지, 목, 등 | 프레임 : S프레...   
3      안마부위 : 어깨, 팔, 허리, 엉덩이, 골반, 종아리, 발, 손, 허벅지, 목, ...   
4      안마부위 : 어깨, 팔, 허리, 엉덩이, 골반, 종아리, 발, 손, 허벅지, 목, ...   
5      안마부위 : 어깨, 팔, 허리, 엉덩이, 골반, 종아리, 발, 손, 허벅지, 목, ...   
...                                                  ...   
96099              스위치 : 버튼스위치 | 소켓종류 : E26 | 소비전력 : 60W   
96579  스위치 : 풋스위치 | 소켓종류 : E26 | 전구종류 : 백열전구 | 소비전력 :...   
97600                                         소켓종류 : E26   
98408               스위치 : 풋스위치 | 소켓종류 : E26 | 소비전력 : 60W   
99122   밝기조절 : 없음 | 스위치 : 풋스위치 | 소켓종류 : E26 | 소비전력 : 60W   

                            imageName  \
0      24895107748.20210607141246.jpg   
1      15383106245.20220204125645.jpg   
3      22542865736.20201109112219.jpg   
4      265

In [ ]:
for i, x in enumerate(np.array_split(pd_crawl_result, 10)):
    x.to_excel(f"네이버쇼핑_크롤링_220117_{i+1}_of_10.xlsx", index = False)

In [19]:
pd.DataFrame(pd_crawl_result["searchCategoryName"].str.split(" > ").value_counts()).to_excel("category_counts_220307.xlsx")

In [27]:
pd_crawl_result["searchCategoryName"].str.split(" > ").apply(lambda x: x[-1]).value_counts().to_excel("category_counts_220307.xlsx")

In [15]:
len(pd_crawl_result["searchCategoryId"].unique())

136

In [7]:
with open(f"crawl_result.pkl", "wb") as f:
    pickle.dump(crawl_result, f)

In [170]:
url = "https://search.shopping.naver.com/catalog/29938164618"

In [171]:
def get_soup(url):
    rq = requests.get(url)
    soup = BeautifulSoup(rq.text, "html.parser")

    return soup

In [245]:
def extract_product_infos(soup):
    infos = soup.find_all("span", attrs={"class" : "top_cell__3DnEV"})
    info_dict = defaultdict(list)
    for info in infos:
        info = info.get_text(strip=True)
        if info == "브랜드 카탈로그":
            continue
        
        if info[:3] in ("브랜드", "제조사"):
            info_dict[info[:3]] = info[3:]

        if ":" in info:
            info_dict[info.split(":")[0]] = info.split(":")[1].split(",")
    return info_dict

In [246]:
dict1 = extract_product_infos(soup)
dict1

defaultdict(list,
            {'제조사': 'LG전자',
             '브랜드': 'LG전자',
             '패널': ['IPS패널'],
             '스마트': ['웹OS', '넷플릭스', '유튜브', '인터넷', '앱스토어', 'Disney+'],
             '부가기능': ['블루투스', '터치스크린'],
             '화면공유': ['스크린미러링'],
             '음향': ['10W(2채널)'],
             '단자': ['USB', '셋톱박스필수(RF여부확인필요)']})

In [178]:
data = pd.read_excel("네이버쇼핑_크롤링_220117.xlsx")

In [240]:
product_info["brand"].isna().values[0]

False

In [262]:
def compare_dict(dict1, dict2):
    keys = np.unique(list(dict1.keys()) + list(dict2.keys()))
    for key in keys:
        if isinstance(dict1[key], list):
            if set(dict1[key]) != set(dict2[key]):
                return False
        else:
            if dict1[key] != dict2[key]:
                return False
    
    return True

In [ ]:
old_data = pd.read_excel("네이버쇼핑_크롤링_220117_상품정보컬럼_모델코드추가.xlsx")

In [22]:
old_data = old_data.drop(["Unnamed: 0"], 1).drop_duplicates()

<ipython-input-22-1231f26c7f8f>:1: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  old_data = old_data.drop(["Unnamed: 0"], 1).drop_duplicates()


In [15]:
import pandas as pd
product_master = pd.read_excel("상품_정보_마스터_220308.xlsx")
target_product_master = product_master.loc[product_master[" 상품 대상여부"].isin(["O", "△"])]
target_product_master.shape

(13231, 19)

In [27]:
pd.merge(target_product_master.drop(["제조사", "브랜드"], axis = 1), old_data[["id", "제조사", "브랜드"]], on = "id", how = "left").to_excel("상품_정보_마스터_220311.xlsx")

In [345]:
[x.strip() for x in "절전, 취침, 온도,습도제어".split(",")]

['절전', '취침', '온도', '습도제어']

In [2]:
class Check_Product_Changes():
    def __init__(self, product_infos):
        self.product_infos = product_infos

    def _extract_info_dict_from_xlsx(self, product_id):
        product_info = self.product_infos.loc[self.product_infos["id"] == product_id, ]
        attrs = product_info["productAttr"].values[0]
        info_dict = {attr.split(" : ")[0] : [x.strip() for x in attr.split(" : ")[1].split(",")] for attr in attrs.split(" | ")}
        if product_info["brand"].isna().values[0] == False:
            info_dict["브랜드"] = product_info["brand"].values[0]
            
        if product_info["maker"].isna().values[0] == False:
            info_dict["제조사"] = product_info["maker"].values[0]
        
        if "" in info_dict.keys():
            del info_dict[""]

        return info_dict


    def _get_soup(self, product_id):
        url = f"https://search.shopping.naver.com/catalog/{product_id}"
        rq = requests.get(url)
        if "존재하지 않습니다." in rq.text:
            return None

        soup = BeautifulSoup(rq.text, "html.parser")

        return soup


    def _extract_info_dict_from_html(self, soup):
        infos = soup.find_all("span", attrs={"class" : "top_cell__3DnEV"})
        info_dict = defaultdict(list)
        for info in infos:
            info = info.get_text(strip=True)
            if info == "브랜드 카탈로그":
                continue
            
            if info[:3] in ("브랜드", "제조사"):
                info_dict[info[:3]] = info[3:]

            if ":" in info:
                info_dict[info.split(":")[0]] = info.split(":")[1].split(",")
        
        return info_dict


    def compare_dict(self, dict1, dict2, verbose = False):
        if set(dict1.keys()) != set(dict2.keys()):
            if verbose:
                dismatch_keys1 = set(dict1.keys()) - set(dict2.keys())
                dismatch_keys2 = set(dict2.keys()) - set(dict1.keys())
                dismatch_keys = dismatch_keys1.union(dismatch_keys2)
                print(f"Key Dismatched ({','.join(dismatch_keys)})")
            return False

        keys = np.unique(list(dict1.keys()) + list(dict2.keys()))
        for key in keys:
            if isinstance(dict1[key], list):
                if set(dict1[key]) != set(dict2[key]):
                    if verbose:
                        print(f"Key({key}) Value Dismatched ({dict1[key]}), ({dict2[key]})")
                    return False
            else:
                if dict1[key] != dict2[key]:
                    if verbose:
                        print(f"Key({key}) Value Dismatched ({dict1[key]}), ({dict2[key]})")
                    return False
        
        return True


    def run_check(self, verbose = False):
        check_list = [None for _ in range(self.product_infos.shape[0])]
        for i, id in enumerate(self.product_infos["id"]):
            print(f"i : {i}, Product ID : {id}, ", end = "")
            self.info_dict_xlsx = self._extract_info_dict_from_xlsx(id)

            soup = self._get_soup(id)
            if soup is None:
                check_list[i] = False
                print(f"상품이 존재하지 않습니다. {check_list[i]},")
                continue
            self.info_dict_html = self._extract_info_dict_from_html(soup)

            check_list[i] = self.compare_dict(self.info_dict_xlsx, self.info_dict_html, verbose = verbose)

            print(check_list[i])
        return check_list


In [3]:
product_id = 22337169761
url = f"https://search.shopping.naver.com/catalog/{product_id}"
rq = requests.get(url)
soup = BeautifulSoup(rq.text, "html.parser")

infos = soup.find_all("span", attrs={"class" : "top_cell__3DnEV"})
info_dict = defaultdict(list)
for info in infos:
    info = info.get_text(strip=True)
    if info == "브랜드 카탈로그":
        continue
    
    if info[:3] in ("브랜드", "제조사"):
        info_dict[info[:3]] = info[3:]

    if ":" in info:
        info_dict[info.split(":")[0]] = info.split(":")[1].split(",")

info_dict

defaultdict(list,
            {'제조사': '캐리어',
             '브랜드': '캐리어',
             '출시년도': ['2019년'],
             '에너지효율': ['3등급'],
             '냉방면적': ['52.8㎡'],
             '냉방능력': ['6', '500W'],
             '소비전력': ['1.55kW'],
             '운전모드': ['절전', '취침', '온도', '습도제어'],
             '풍량조절': ['18단에어컨트롤'],
             '냉방': ['쾌속', '트리플컨트롤', '하이브리드팬'],
             '스마트기능': ['음성인식', '스마트폰제어(옵션)'],
             '인공지능': ['PMV운전', '가능'],
             '공기청정': ['프리필터', '카본필터', '정전필터'],
             '제습': ['가능'],
             '힐링': ['솔솔바람'],
             '에어컨청소': ['자동건조'],
             '스타일': ['에어로18단'],
             '토출구': ['좌우'],
             '품목': ['스탠드형에어컨']})

In [4]:
sample_df = pd.read_excel("raw_sample_product_infos.xlsx")
product_changes = Check_Product_Changes(product_infos = sample_df.loc[sample_df["id"] == 22337169761]) # 
product_changes.run_check(verbose=True)


i : 0, Product ID : 22337169761, True


[True]

In [6]:
data = pd.read_excel("네이버쇼핑_크롤링_220117.xlsx")

In [8]:
atoms = 10
[(2*(i-1)+1)/(2*atoms) for i in range(1, atoms+1)]

[0.05, 0.15, 0.25, 0.35, 0.45, 0.55, 0.65, 0.75, 0.85, 0.95]

In [7]:
sample_df = pd.read_excel("raw_sample_product_infos.xlsx")
product_changes = Check_Product_Changes(product_infos = sample_df) # .loc[sample_df["id"] == 27429048055]
changes = product_changes.run_check(verbose=True)

i : 0, Product ID : 24895107748, True
i : 1, Product ID : 16924785110, Key(안마방식) Value Dismatched (['주무름', '두드림', '공기압', '진동', '지압']), (['주무름', '두드림', '공기압', '진동'])
False
i : 2, Product ID : 15383106245, True
i : 3, Product ID : 15618287432, True
i : 4, Product ID : 19652900156, True
i : 5, Product ID : 25371389874, True
i : 6, Product ID : 15382974698, True
i : 7, Product ID : 28884765586, True
i : 8, Product ID : 22542865736, True
i : 9, Product ID : 27429048055, True
i : 10, Product ID : 23604347490, True
i : 11, Product ID : 28621724375, True
i : 12, Product ID : 25779070831, True
i : 13, Product ID : 22507481085, True
i : 14, Product ID : 20834164385, True
i : 15, Product ID : 25719090704, True
i : 16, Product ID : 23369457491, True
i : 17, Product ID : 20513967165, True
i : 18, Product ID : 25610813675, True
i : 19, Product ID : 17563047346, True
i : 20, Product ID : 22544338950, True
i : 21, Product ID : 28688511396, True
i : 22, Product ID : 17562942554, True
i : 23, Product ID

In [292]:
data.loc[data["id"] == 24063567165, ["brand", "maker"]]

brand maker
17   휴테크   휴테크

In [3]:
data_old = pd.read_excel("네이버쇼핑_크롤링_220117.xlsx")
data_new = pd.read_excel("네이버쇼핑_크롤링_220207.xlsx")

In [12]:
product_model_list = []
for product_name in data_new["productName"]:
    product_model = None
    tokens = re.subn(r"\(.*\)|", "", product_name)[0].strip().split(" ")
    if re.search(r"[가-힣]",tokens[-1]) is None:
        product_model = tokens[-1]
    product_model_list.append(product_model)

In [13]:
data_new["modelCode"] = product_model_list

In [8]:
len(product_model_list)

241744

In [ ]:
기존 : 241744
신규 : 241133
공통 id : 69704
값이 바뀐 것 : 6009
제품 스펙 정보 변경 : 583
제조사 정보 변경 : 491 
브랜드 정보 변경 : 295 

In [123]:
data_new.

0          NaN
1          NaN
2          NaN
3          NaN
4          NaN
          ... 
241739    장스탠드
241740    장스탠드
241741    장스탠드
241742    장스탠드
241743    장스탠드
Name: category4Name, Length: 241744, dtype: object

In [33]:
new_info.values

array([['프리미엄 이어폰', 'COSONIC', 37385, 'COSONIC', 37386, nan,
        '부가기능 : 통화가능 | 선형태 : 발란스(Y)형 | 커넥터 : 일자형(SP) | 임피던스 : 16Ohms']],
      dtype=object)

ValueError: The truth value of an array with more than one element is ambiguous. Use a.any() or a.all()

In [95]:
temp = [x for x in changed_infos if len(x[2]) != 0 ]

changed_cols_df = pd.DataFrame(temp, columns = ["index", "productid", "changed_cols"])
changed_cols_df.loc[changed_cols_df["changed_cols"].apply(lambda x: "productAttr" in x)]

index    productid                           changed_cols
8       140  27330740524                          [productAttr]
9       146  27392606523                          [productAttr]
10      156   1000079695                          [productAttr]
22      266  25276842522                  [lnchYm, productAttr]
52      694  27330741522                          [productAttr]
...     ...          ...                                    ...
5937  68870  25066076524                          [productAttr]
5965  69219  22954900490  [maker, makerNo, lnchYm, productAttr]
5979  69348  29488184618                          [productAttr]
5980  69351  28971105586                          [productAttr]
6002  69628  27439005522                          [productAttr]

[583 rows x 3 columns]

In [86]:
changed_infos = []
for i, id in enumerate(common_id):
    new_info = data_new.loc[data_new["id"] == id, ["productName", "maker", "makerNo", "brand", "brandNo", "lnchYm", "productAttr"]].values[0]
    old_info = data_old.loc[data_old["id"] == id, ["productName", "maker", "makerNo", "brand", "brandNo", "lnchYm", "productAttr"]].values[0]

    print(f"index = {i}, id : {id}", end = " ")
    temp = []
    for j, x in enumerate(["productName", "maker", "makerNo", "brand", "brandNo", "lnchYm", "productAttr"]):
        if new_info[j] is np.nan:
            new_info[j] = ""
        if old_info[j] is np.nan:
            old_info[j] = ""

        if new_info[j] != old_info[j]:
            temp.append(x)
            print(x, end = ", ")
    changed_infos.append([i, id, temp])
    print("")


index = 0, id : 10802298881 lnchYm, 
index = 1, id : 25039339522 
index = 2, id : 30409883649 
index = 3, id : 30565859333 
index = 4, id : 7219052551 
index = 5, id : 30301356040 
index = 6, id : 9096396812 
index = 7, id : 28645392398 
index = 8, id : 23439081490 
index = 9, id : 5980815382 
index = 10, id : 24067178522 
index = 11, id : 17584881695 
index = 12, id : 7692877856 
index = 13, id : 5983567903 lnchYm, 
index = 14, id : 17830641698 
index = 15, id : 17830641699 
index = 16, id : 26408255524 lnchYm, 
index = 17, id : 9756213285 
index = 18, id : 10933108773 
index = 19, id : 13271171111 
index = 20, id : 25190465578 
index = 21, id : 27520532524 
index = 22, id : 10396762157 
index = 23, id : 19277021230 
index = 24, id : 25914900526 
index = 25, id : 26322665524 
index = 26, id : 23397138491 
index = 27, id : 29460267068 
index = 28, id : 19449905213 
index = 29, id : 6207963198 lnchYm, 
index = 30, id : 4134142015 lnchYm, 
index = 31, id : 21287010368 
index = 32, id : 1

In [109]:
data_new.loc[data_new["id"] == 19868549255]

Empty DataFrame
Columns: [searchCategoryId, searchCategoryName, id, productName, scoreInfo, category1Id, category2Id, category3Id, category4Id, category1Name, category2Name, category3Name, category4Name, maker, makerNo, brand, brandNo, price, priceUnit, lnchYm, productAttr, imageName, crUrl, imageUrl]
Index: []

[0 rows x 24 columns]

In [119]:
data_old.loc[data_old["id"] == 30395072604]

searchCategoryId  searchCategoryName           id  \
8076          50001830  생활/건강 > 안마용품 > 안마기  30395072604   

                productName  scoreInfo  category1Id  category2Id  category3Id  \
8076  눈 마사지기 피로해소 온찜질 안구건조증        NaN     50000008     50000075     50001830   

      category4Id category1Name  ... makerNo brand brandNo  price  priceUnit  \
8076          NaN         생활/건강  ...       0   NaN       0  47790        KRW   

          lnchYm  productAttr                       imageName  \
8076  20220103.0           :   30395072604.20220103004827.jpg   

                                                  crUrl  \
8076  https://cr.shopping.naver.com/adcr.nhn?x=qo34o...   

                                               imageUrl  
8076  https://shopping-phinf.pstatic.net/main_303950...  

[1 rows x 24 columns]

In [116]:
data_new.loc[data_new["productName"].str.contains("보이로")]

Empty DataFrame
Columns: [searchCategoryId, searchCategoryName, id, productName, scoreInfo, category1Id, category2Id, category3Id, category4Id, category1Name, category2Name, category3Name, category4Name, maker, makerNo, brand, brandNo, price, priceUnit, lnchYm, productAttr, imageName, crUrl, imageUrl]
Index: []

[0 rows x 24 columns]

In [104]:
set(data_old["id"]) - set(data_new["id"])

{30299914243,
 30394810371,
 29582426117,
 30459035659,
 30317871122,
 30431248413,
 30394810402,
 30565204005,
 30061756454,
 30397300777,
 30490492985,
 30316560464,
 30247616594,
 30395072604,
 30233198699,
 30306336886,
 30044192888,
 30462836857,
 30357848198,
 19868549255,
 30478827661,
 29553197198,
 30395072657,
 30435836050,
 30565859475,
 30306992279,
 26458980522,
 29276766387,
 30406213823,
 30359945408,
 22385918153,
 25727598794,
 30431641804,
 30318002393,
 30043406557,
 20349059296,
 30356799723,
 30532829429,
 30063853814,
 30318133497,
 30458773774,
 30565859607,
 18007327003,
 30565859613,
 30481580333,
 30247616826,
 30431772987,
 30481449279,
 30064378185,
 30410670413,
 30297162068,
 30490493279,
 4059693410,
 30410146164,
 30286807420,
 29908009342,
 30532567426,
 30299914629,
 30471618950,
 30260593039,
 29870129553,
 30045372820,
 30290346396,
 30459822497,
 30458773925,
 30061887910,
 30478827942,
 30148657581,
 30290346416,
 30289166772,
 30461788600,
 304056

In [12]:
set(data_new["id"]) - set(data_old["id"])

{30619598849,
 30817648643,
 30817648647,
 30666653713,
 30817648662,
 30666129434,
 30720393246,
 30827741226,
 30719737907,
 30656430133,
 30666129464,
 30756044864,
 30742151248,
 30666391636,
 30806245462,
 30646730841,
 30742413414,
 30655250540,
 30819483776,
 30806245525,
 30755651737,
 16943022252,
 30755520687,
 30796021939,
 30755913908,
 30817386680,
 26458980540,
 30816993468,
 30719213757,
 30619599040,
 30796021961,
 30720393437,
 30621565152,
 30745034977,
 30818042090,
 30656430321,
 30794711283,
 30633623802,
 30757486843,
 30719344907,
 30756176146,
 6706299160,
 30644633889,
 30817648938,
 30817517868,
 30710038838,
 30745035068,
 30644764991,
 30666391883,
 30806376780,
 30406476110,
 30693785938,
 30827872597,
 30720131416,
 30818828633,
 30706762077,
 30818828647,
 10732962155,
 30605181293,
 30796022134,
 30719213945,
 30707155328,
 30820532625,
 4068344215,
 30636507544,
 30742544798,
 30816469408,
 30755783076,
 30619599273,
 5922226608,
 30713053620,
 30826824

In [27]:
common_id = set(data_new["id"]).intersection(set(data_old["id"]))
len(common_id)

69704

In [6]:
data_new.head()

searchCategoryId   searchCategoryName           id  \
0          50001828  생활/건강 > 안마용품 > 안마의자  22542865736   
1          50001828  생활/건강 > 안마용품 > 안마의자  24895107748   
2          50001828  생활/건강 > 안마용품 > 안마의자  15618287432   
3          50001828  생활/건강 > 안마용품 > 안마의자  16924785110   
4          50001828  생활/건강 > 안마용품 > 안마의자  15383106245   

                  productName  scoreInfo  category1Id  category2Id  \
0            컴포어 안마의자 HT-N02A        4.7     50000008     50000075   
1        이지움 노블 안마의자 LS-6700N        4.8     50000008     50000075   
2      트윈 소형 미니 안마의자 HCW-5000        4.7     50000008     50000075   
3  뉴블리스 2021년형 안마의자 HCW-6000S        4.8     50000008     50000075   
4   이지움 벨라 소형 미니 안마의자 LS-2900        4.7     50000008     50000075   

   category3Id  category4Id category1Name  ... makerNo brand brandNo    price  \
0     50001828          NaN         생활/건강  ...    7755   휴테크  137710  1250000   
1     50001828          NaN         생활/건강  ...       0    리쏘  149453  1160570   
2     50001828          NaN         생활/건강  ...  212668   웰모아  212667   658600   
3     50001828          NaN         생활/건강  ...  212668   웰모아  212667  1218000   
4     50001828          NaN         생활/건강  ...  191573    리쏘  149453   650320   

   priceUnit      lnchYm                                        productAttr  \
0        KRW  20200401.0  안마부위 : 어깨, 팔, 허리, 엉덩이, 골반, 종아리, 발, 손, 허벅지, 목, ...   
1        KRW  20201118.0  안마부위 : 어깨, 팔, 허리, 엉덩이, 골반, 종아리, 발, 손, 허벅지, 목, ...   
2        KRW  20181008.0  안마부위 : 허리, 엉덩이, 골반, 종아리, 허벅지, 등 | 프레임 : S프레임, ...   
3        KRW  20190107.0  안마부위 : 어깨, 팔, 허리, 엉덩이, 골반, 종아리, 발, 손, 허벅지, 목, ...   
4        KRW  20180901.0  안마부위 : 허리, 엉덩이, 골반, 종아리, 허벅지, 목, 등 | 프레임 : S프레...   

                        imageName  \
0  22542865736.20201109112219.jpg   
1  24895107748.20210607141246.jpg   
2  15618287432.20210810175114.jpg   
3  16924785110.20210817181802.jpg   
4  15383106245.20220204125645.jpg   

                                               crUrl  \
0  https://cr.shopping.naver.com/adcr.nhn?x=ScKdN...   
1  https://cr.shopping.naver.com/adcr.nhn?x=7V0DU...   
2  https://cr.shopping.naver.com/adcr.nhn?x=yh8sw...   
3  https://cr.shopping.naver.com/adcr.nhn?x=DRJNV...   
4  https://cr.shopping.naver.com/adcr.nhn?x=SZpZv...   

                                            imageUrl  
0  https://shopping-phinf.pstatic.net/main_225428...  
1  https://shopping-phinf.pstatic.net/main_248951...  
2  https://shopping-phinf.pstatic.net/main_156182...  
3  https://shopping-phinf.pstatic.net/main_169247...  
4  https://shopping-phinf.pstatic.net/main_153831...  

[5 rows x 24 columns]

In [3]:
data_old.shape

(241133, 24)